### Question3: MDP
- Note that each iteration is taking around 4sec if size = (10, 5, 5) and 7 minute if size = (20, 10, 10).
- Method:
> Indefinitte Value Iteration. 

In [3]:
import itertools
import numpy as np
# from tqdm import tqdm, tqdm_notebook
import copy

In [11]:
import itertools
import numpy as np
# from tqdm import tqdm, tqdm_notebook
import copy

def poisson(lambda1, n):
    return (np.power(lambda1, n)/np.math.factorial(n))*(np.exp(-lambda1))

##########CONSTANTS###########
requestLambda = [3, 2, 2]
returnLambda = [3, 1, 1]

#Number of maximum cars allowed at loc1, loc2, loc3
ml1, ml2, ml3 = 20, 10, 10

gamma = 0.9
numIter = 10
tol = 0.01
Size = (ml1, ml2, ml3)

n1 = np.arange(ml1)
n2 = np.arange(ml2)
n3 = np.arange(ml3)
n4 = np.arange(-5, 6)
#=============================#

#================PreCalculations of Probability and Rewards============#
JointProbLocation1 = np.ones((ml1, ml1, ml1, ml1))*0
JointProbLocation2 = np.ones((ml2, ml2, ml2, ml2))*0
JointProbLocation3 = np.ones((ml3, ml3, ml3, ml3))*0
JointRewardLocation1 = np.ones((ml1, ml1, ml1, ml1))*0
JointRewardLocation2 = np.ones((ml2, ml2, ml2, ml2))*0
JointRewardLocation3 = np.ones((ml3, ml3, ml3, ml3))*0

ProbRequestLocation1 = np.asarray([poisson(requestLambda[0], i) for i in range(ml1)])
ProbRequestLocation2 = np.asarray([poisson(requestLambda[1], i) for i in range(ml2)])
ProbRequestLocation3 = np.asarray([poisson(requestLambda[2], i) for i in range(ml3)])

RewardRequestLocation1 = np.asarray([poisson(requestLambda[0], i)*i*10 for i in range(ml1)])
RewardRequestLocation2 = np.asarray([poisson(requestLambda[1], i)*i*10 for i in range(ml2)])
RewardRequestLocation3 = np.asarray([poisson(requestLambda[2], i)*i*10 for i in range(ml3)])

ProbReturnLocation1 = np.asarray([poisson(returnLambda[0], i) for i in range(ml1)])
ProbReturnLocation2 = np.asarray([poisson(returnLambda[1], i) for i in range(ml2)])
ProbReturnLocation3 = np.asarray([poisson(returnLambda[2], i) for i in range(ml3)])


for (reqStart, reqEnd, retStart, retEnd) in itertools.product(n1, n1, n1, n1):  #start, End inclusive
    if(reqEnd - reqStart + 1 != retEnd - retStart + 1):
        continue
        
    JointProbLocation1[reqStart, reqEnd, retStart, retEnd] = np.sum(
        ProbRequestLocation1[reqStart:reqEnd+1]*ProbReturnLocation1[retStart:retEnd+1])
    JointRewardLocation1[reqStart, reqEnd, retStart, retEnd] = np.sum(
        RewardRequestLocation1[reqStart:reqEnd+1]*ProbReturnLocation1[retStart:retEnd+1])
    
for (reqStart, reqEnd, retStart, retEnd) in itertools.product(n2, n2, n2, n2):
    if(reqEnd - reqStart + 1 != retEnd - retStart + 1):
        continue
    
    JointProbLocation2[reqStart, reqEnd, retStart, retEnd] = np.sum(
        ProbRequestLocation2[reqStart:reqEnd+1]*ProbReturnLocation2[retStart:retEnd+1])
    JointRewardLocation2[reqStart, reqEnd, retStart, retEnd] = np.sum(
        RewardRequestLocation2[reqStart:reqEnd+1]*ProbReturnLocation2[retStart:retEnd+1])
    
for (reqStart, reqEnd, retStart, retEnd) in itertools.product(n3, n3, n3, n3):
    if(reqEnd - reqStart + 1 != retEnd - retStart + 1):
        continue
    
    JointProbLocation3[reqStart, reqEnd, retStart, retEnd] = np.sum(
        ProbRequestLocation3[reqStart:reqEnd+1]*ProbReturnLocation3[retStart:retEnd+1])
    JointRewardLocation3[reqStart, reqEnd, retStart, retEnd] = np.sum(
        RewardRequestLocation3[reqStart:reqEnd+1]*ProbReturnLocation3[retStart:retEnd+1])

#=========================_________________________========================#

class State:
    def __init__(self, car1, car2, car3):
        self.car1 = car1
        self.car2 = car2
        self.car3 = car3
        
def normInfinity(currValue, optimalValue):
    maxDiff = np.max(np.abs(currValue - optimalValue))
    return maxDiff
        

def isValidState(car1, car2, car3):
     return car1 >= 0 and car2 >=0 and car3 >=0 and car1 <ml1 and car2 < ml2 and car3 < ml3
    
def normalize(car1, car2, car3):
    car1 = min(car1, ml1 - 1)
    car2 = min(car2, ml2 - 1)
    car3 = min(car3, ml3 - 1)
    
    return car1, car2, car3

def getCost(mv1, mv2, mv3):
    cost = np.abs(mv1)*2
    return cost

MOVES = []
for mv1, mv2, mv3 in itertools.product(n4, n4, n4):
    if(mv1 + mv2 + mv3 != 0):
        continue
    MOVES.append((mv1, mv2, mv3))


#================================ Value Iteration ===========================#
def ValueIteration(V, Policy):
    for iter1 in (range(numIter)):
        oldV = V.copy()
        print("iter: ", iter1)
        a = time.time()
        #State value
        for i, j, k in itertools.product(n1, n2, n3):
            maxReward = -10000.0
            for (mv1, mv2, mv3) in MOVES:
#                 print("move1 = ", mv1, mv2, mv3)
                reward = 0.0
                car1 = i + mv1
                car2 = j + mv2
                car3 = k + mv3
#                 print(i, j, k, car1, car2, car3)
                
                if(not isValidState(car1, car2, car3)):
                    continue
                
                reward-=getCost(mv1, mv2, mv3)
#                 print("Move2 = ", mv1, mv2, mv3)
                
                for i1, j1, k1 in itertools.product(n1, n2, n3):
                    reqStart = max(0, car1 - i1)
                    retStart = max(0, i1 - car1)
                    retEnd = i1
                    p1_sum = JointProbLocation1[reqStart, car1, retStart, retEnd]
                    r1_sum = JointRewardLocation1[reqStart, car1, retStart, retEnd]
                    reqStart = max(0, car2 - j1)
                    retStart = max(0, j1 - car2)
                    retEnd = j1
                    p2_sum = JointProbLocation2[reqStart, car2, retStart, retEnd]
                    r2_sum = JointRewardLocation2[reqStart, car2, retStart, retEnd]
                    reqStart = max(0, car3 - k1)
                    retStart = max(0, k1 - car3)
                    retEnd = k1
                    p3_sum = JointProbLocation3[reqStart, car3, retStart, retEnd]
                    r3_sum = JointRewardLocation3[reqStart, car3, retStart, retEnd]

                    immediateReward = p1_sum*p2_sum*r3_sum + p1_sum*r2_sum*p3_sum + r1_sum*p2_sum*p3_sum
                    reward+= immediateReward + gamma*p1_sum*p2_sum*p3_sum*oldV[i1, j1, k1] 
                if(reward > maxReward):
                    maxReward = reward
#                     print("here")
                    Policy[i, j, k] = np.array([mv1, mv2, mv3])
            V[i, j, k] = maxReward 
            
        if(normInfinity(V, oldV) <= 0.1):
            print("Converged in {} iteration".format(iter1 + 2))
            break
        print(time.time() - a)
    return V, Policy
#============================ _________________________ ===================#

In [7]:
import time
Size = (ml1, ml2, ml3)
Value = np.zeros(Size)
Policy = np.zeros(Size + tuple([3]))
a = time.time()
V, P = ValueIteration(Value, Policy)
print("Time Taken = ",time.time() - a)
np.savetxt("Value.txt", np.ravel(V).reshape(50, 5), fmt = "%.2f", header = 'values')
np.savetxt("Policy.txt", np.ravel(P).reshape(250, 3), fmt = "%i")
print("Value.txt Saved")
print("Policy.txt Saved")

NameError: name 'ValueIteration' is not defined

#### Appproach2 for PreCalculation

In [25]:
##########CONSTANTS###########
requestLambda = [3, 2, 2]
returnLambda = [3, 1, 1]

#Number of maximum cars allowed at loc1, loc2, loc3
# ml1, ml2, ml3 = 20, 10, 10
ml1, ml2, ml3 = 10, 5, 5

gamma = 0.9
numIter = 10
tol = 0.01
Size = (ml1, ml2, ml3)

n1 = np.arange(ml1)
n2 = np.arange(ml2)
n3 = np.arange(ml3)
n4 = np.arange(-5, 6)
#=============================#

#================PreCalculations of Probability and Rewards============#
JointProbLocation1 = np.ones((ml1, ml1))*0
JointProbLocation2 = np.ones((ml2, ml2))*0
JointProbLocation3 = np.ones((ml3, ml3))*0
JointRewardLocation1 = np.ones((ml1, ml1))*0
JointRewardLocation2 = np.ones((ml2, ml2))*0
JointRewardLocation3 = np.ones((ml3, ml3))*0

ProbRequestLocation1 = np.asarray([poisson(requestLambda[0], i) for i in range(ml1)])
ProbRequestLocation2 = np.asarray([poisson(requestLambda[1], i) for i in range(ml2)])
ProbRequestLocation3 = np.asarray([poisson(requestLambda[2], i) for i in range(ml3)])

RewardRequestLocation1 = np.asarray([poisson(requestLambda[0], i)*i*10 for i in range(ml1)])
RewardRequestLocation2 = np.asarray([poisson(requestLambda[1], i)*i*10 for i in range(ml2)])
RewardRequestLocation3 = np.asarray([poisson(requestLambda[2], i)*i*10 for i in range(ml3)])

ProbReturnLocation1 = np.asarray([poisson(returnLambda[0], i) for i in range(ml1)])
ProbReturnLocation2 = np.asarray([poisson(returnLambda[1], i) for i in range(ml2)])
ProbReturnLocation3 = np.asarray([poisson(returnLambda[2], i) for i in range(ml3)])


for (currState, nextState) in itertools.product(n1, n1):  
    for request, ret in itertools.product(n1, n1):
        if(request > currState or currState-request+ret != nextState):
            continue
        JointProbLocation1[currState, nextState] += (ProbRequestLocation1[request]
                            *ProbReturnLocation1[ret])
        JointRewardLocation1[currState, nextState] += (ProbRequestLocation1[request]
                            *ProbReturnLocation1[ret])*request*10
            
for (currState, nextState) in itertools.product(n2, n2):  
    for request, ret in itertools.product(n2, n2):
        if(request > currState or currState-request+ret != nextState):
            continue
        JointProbLocation2[currState, nextState] += (ProbRequestLocation2[request]
                            *ProbReturnLocation2[ret])
        JointRewardLocation2[currState, nextState] += (ProbRequestLocation3[request]
                            *ProbReturnLocation2[ret])*request*10

for (currState, nextState) in itertools.product(n3, n3):  
    for request, ret in itertools.product(n3, n3):
        if(request > currState or currState-request+ret != nextState):
            continue
        JointProbLocation3[currState, nextState] += (ProbRequestLocation3[request]
                            *ProbReturnLocation3[ret])
        JointRewardLocation3[currState, nextState] += (ProbRequestLocation3[request]
                            *ProbReturnLocation3[ret])*request*10
#=========================_________________________========================#
        
def normInfinity(currValue, optimalValue):
    maxDiff = np.max(np.abs(currValue - optimalValue))
    return maxDiff
        

def isValidState(car1, car2, car3):
     return car1 >= 0 and car2 >=0 and car3 >=0 and car1 <ml1 and car2 < ml2 and car3 < ml3

def getCost(mv1, mv2, mv3):
    cost = np.abs(mv1)*2
    return cost

MOVES = []
for mv1, mv2, mv3 in itertools.product(n4, n4, n4):
    if(mv1 + mv2 + mv3 != 0):
        continue
    MOVES.append((mv1, mv2, mv3))


#================================ Value Iteration ===========================#
def ValueIteration(V, Policy):
    for iter1 in (range(numIter)):
        oldV = V.copy()
        print("iter: ", iter1)
        a = time.time()
        #State value
        for i, j, k in itertools.product(n1, n2, n3):
            maxReward = -10000.0
            for (mv1, mv2, mv3) in MOVES:
#                 print("move1 = ", mv1, mv2, mv3)
                reward = 0.0
                car1 = i + mv1
                car2 = j + mv2
                car3 = k + mv3
#                 print(i, j, k, car1, car2, car3)
                
                if(not isValidState(car1, car2, car3)):
                    continue
                
                reward-=getCost(mv1, mv2, mv3)
                
                for i1, j1, k1 in itertools.product(n1, n2, n3):
                    p1_sum = JointProbLocation1[car1, i1]
                    r1_sum = JointRewardLocation1[car1, i1]
                    
                    p2_sum = JointProbLocation2[car2, j1]
                    r2_sum = JointRewardLocation2[car2, j1]
                    
                    p3_sum = JointProbLocation3[car3, k1]
                    r3_sum = JointRewardLocation3[car3, k1]
                    print("oldV : ", gamma*p1_sum*p2_sum*p3_sum*oldV[i1, j1, k1])
                    immediateReward = p1_sum*p2_sum*r3_sum + p1_sum*r2_sum*p3_sum + r1_sum*p2_sum*p3_sum
                    reward+= immediateReward + gamma*p1_sum*p2_sum*p3_sum*oldV[i1, j1, k1] 
                if(reward > maxReward):
                    maxReward = reward
                    Policy[i, j, k] = np.array([mv1, mv2, mv3])
            V[i, j, k] = maxReward 
            print("max : ", maxReward)
        
        if(normInfinity(V, oldV) <= 0.1):
            print("Converged in {} iteration".format(iter1 + 2))
            break
        print(time.time() - a)
    return V, Policy

In [21]:
np.max(JointProbLocation1)
# JointProbLocation1

0.16665672425438807

In [22]:
# JointRewardLocation1

In [23]:
# JointRewardLocation2

In [26]:
import time
Size = (ml1, ml2, ml3)
Value = np.zeros(Size)
Policy = np.zeros(Size + tuple([3]))
a = time.time()
V, P = ValueIteration(Value, Policy)
print("Time Taken = ",time.time() - a)
np.savetxt("Value1.txt", np.ravel(V).reshape(50, 5), fmt = "%.2f", header = 'values')
np.savetxt("Policy1.txt", np.ravel(P).reshape(250, 3), fmt = "%i")
print("Value1.txt Saved")
print("Policy1.txt Saved")

iter:  0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV : 

oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV

oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV

oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV

oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV

...

oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV

oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV

oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV

oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV :  0.0
oldV

KeyboardInterrupt: 

---